In [61]:
import re
from typing import List, Union, Tuple
from nltk.corpus import stopwords as stpwrds
from sklearn.model_selection import train_test_split
import time
from os.path import isfile
import numpy as np
# Webscraping
from bs4 import BeautifulSoup
from requests import get
import seaborn as sns
import pandas as pd
import nltk
import unicodedata
import nltk.sentiment


import os

import matplotlib.pyplot as plt
import json
from typing import Dict, List, Optional, Union, cast
import requests
import prepare as p
from nltk.tokenize.toktok import ToktokTokenizer

from scipy import stats
import acquire as w

In [62]:
df = w.get_michelin_pages()

In [63]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6780 entries, 0 to 6779
Data columns (total 13 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   name                     6780 non-null   object 
 1   address                  6780 non-null   object 
 2   location                 6780 non-null   object 
 3   price                    6726 non-null   object 
 4   cuisine                  6780 non-null   object 
 5   longitude                6780 non-null   float64
 6   latitude                 6780 non-null   float64
 7   phone_number             6649 non-null   float64
 8   url                      6780 non-null   object 
 9   website_url              5542 non-null   object 
 10  award                    6780 non-null   object 
 11  facilities_and_services  6732 non-null   object 
 12  data                     6780 non-null   object 
dtypes: float64(3), object(10)
memory usage: 688.7+ KB


In [64]:
train, validate, test = p.prepare_michelin(df)

In [65]:
# create sentimate dataframe for 
sentiment_df1 = train[['award','lemmatized']]

In [66]:
# create sentimate dataframe for 
sentiment_df2 = validate[['award','lemmatized']]

In [67]:
# create sentimate dataframe for 
sentiment_df3 = test[['award','lemmatized']]

In [68]:
def get_sentiment(sentiment_df1, sentiment_df2, sentiment_df3):
    '''Function calculates sentiment score and creates dataframe of scores'''
    # reindex dataframe
    sentiment_df1.reset_index(drop =True, inplace=True)
    sentiment_df2.reset_index(drop =True, inplace=True)
    sentiment_df3.reset_index(drop =True, inplace=True)
    #create sentiment object
    sia = nltk.sentiment.SentimentIntensityAnalyzer()
    # create row id column
    sentiment_df1["row_id"] =sentiment_df1.index +1  
    sentiment_df2["row_id"] =sentiment_df2.index +1  
    sentiment_df3["row_id"] =sentiment_df3.index +1  
    # create subsets
    df_subset1 = sentiment_df1[['row_id', 'lemmatized']].copy() 
    df_subset2 = sentiment_df2[['row_id', 'lemmatized']].copy()
    df_subset3 = sentiment_df3[['row_id', 'lemmatized']].copy()
    # set up empty dataframe for staging output
    df1=pd.DataFrame()
    df1['row_id']=['99999999999']
    df1['sentiment_type']='NA999NA'
    df1['sentiment_score']=0
    
    # run loop to calculate and save sentiment values
    t_df = df1
    for index,row in df_subset1.iterrows():
        scores = sia.polarity_scores(row[1])
        for key, value in scores.items():
            temp = [key,value,row[0]]
            df1['row_id']=row[0]
            df1['sentiment_type']=key
            df1['sentiment_score']=value
            t_df=t_df.append(df1)
    for index,row in df_subset2.iterrows():
        scores = sia.polarity_scores(row[1])
        for key, value in scores.items():
            temp = [key,value,row[0]]
            df1['row_id']=row[0]
            df1['sentiment_type']=key
            df1['sentiment_score']=value
            t_df=t_df.append(df1)
    for index,row in df_subset3.iterrows():
        scores = sia.polarity_scores(row[1])
        for key, value in scores.items():
            temp = [key,value,row[0]]
            df1['row_id']=row[0]
            df1['sentiment_type']=key
            df1['sentiment_score']=value
            t_df=t_df.append(df1)
    #remove dummy row with row_id = 99999999999
    t_df_cleaned = t_df[t_df.row_id != '99999999999']
    #remove duplicates if any exist
    t_df_cleaned = t_df_cleaned.drop_duplicates()
    # only keep rows where sentiment_type = compound
    t_df_cleaned = t_df[t_df.sentiment_type == 'compound']
    
    df_output = pd.merge(sentiment_df1, sentiment_df2, sentiment_df3, t_df_cleaned, on='row_id', how='inner')
    
    #generate mean of sentiment_score by period
  
    dfg = df_output.groupby(['award'])['sentiment_score'].mean()
    #create a bar plot
    dfg.plot(kind='bar', title='Sentiment Score', ylabel='Mean Sentiment Score',
         xlabel='',fontsize =20,color=['#beaed4','#f0027f','#7fc97f','#fdc086'])
    plt.xticks(fontsize=20)
    plt.yticks(fontsize=22)
    plt.show()
   
    return df_output;

In [69]:
get_sentiment(sentiment_df1, sentiment_df2, sentiment_df3)

/var/folders/hb/h75yrttj2jx98ftlw744r4hm0000gn/T/ipykernel_45712/3612578722.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sentiment_df1["row_id"] =sentiment_df1.index +1
/var/folders/hb/h75yrttj2jx98ftlw744r4hm0000gn/T/ipykernel_45712/3612578722.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sentiment_df2["row_id"] =sentiment_df2.index +1
/var/folders/hb/h75yrttj2jx98ftlw744r4hm0000gn/T/ipykernel_45712/3612578722.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice f

TypeError: merge() got multiple values for argument 'on'